In [ ]:
# embeddings from Leon

In [2]:
library(dplyr)
library(stringr)
library(data.table)

In [3]:
path0 = '/grid/gillis/data_norepl/lfrench/heart_embed_transfer/'
list.files(path0)

[1] "Anolis Sagrei.GCF_025583915.1_AnoSag2.1_protein.faa.ProtT5.embeddings.csv.gz"
[2] "Chicken.UP000000539_9031.fasta.ProtT5.embeddings.csv.gz"                     
[3] "Chrysemys picta bellii.UP000694380_8478.fasta.ProtT5.embeddings.csv.gz"      
[4] "Drosophila melanogaster.UP000000803_7227.fasta.ProtT5.embeddings.csv.gz"     
[5] "Human.UP000005640_9606.fasta.ProtT5.embeddings.csv.gz"                       
[6] "Mouse.UP000000589_10090.fasta.ProtT5.embeddings.csv.gz"                      
[7] "Xenopus tropicalis.UP000008143_8364.fasta.ProtT5.embeddings.csv.gz"          
[8] "Zebrafish.UP000000437_7955.fasta.ProtT5.embeddings.csv.gz"

In [6]:
tab1 = fread(paste0(path0, 'Chrysemys picta bellii.UP000694380_8478.fasta.ProtT5.embeddings.csv.gz'))
tab1 <- tab1[-1,]
dim(tab1)

tab1[1:2,]

[1] 21164  1025

V1                                                                                                                       
1 tr|A0A8C3IPM8|A0A8C3IPM8_CHRPI LY6/PLAUR domain containing 6B OS=Chrysemys picta bellii OX=8478 GN=LYPD6B PE=4 SV=1      
2 tr|A0A8C3HU26|A0A8C3HU26_CHRPI Vesicle-associated membrane protein 2 OS=Chrysemys picta bellii OX=8478 GN=VAMP2 PE=3 SV=1
  V2         V3         V4         V5          V6          V7        
1 0.04380944 0.04666854 0.01967055 0.010638186 -0.01983896 0.02670864
2 0.04984607 0.10822530 0.13385898 0.009055086 -0.04259114 0.08893719
  V8          V9          V10         ⋯ V1016       V1017       V1018       
1 -0.04212752 -0.09735513  0.01551907 ⋯ -0.01836805 -0.00636565  0.006043086
2  0.02212998 -0.10179134 -0.07352224 ⋯  0.03350077 -0.07541211 -0.065250990
  V1019       V1020       V1021       V1022       V1023       V1024        
1 -0.08258347  0.04174648  0.04077775 -0.01465437 0.002306046  1.563247e-03
2 -0.05719687 -0.02992775 -0.01860927 -0.01088253 0.024169970 -7.653655e-05
  V1025     
1 0.02171617
2 0.03049799

In [7]:
length(grep('GN=', unlist(tab1[,1])))

[1] 14486

In [76]:
# get uniprot IDs and gene names
vec1 = c()
vec2 = c()
pb = txtProgressBar(min = 0, max = dim(tab1)[1], initial = 0)

for(ii in 1:dim(tab1)[1]){
    pattern <- "GN=\\s*(.*?)\\s* "
    result <- regmatches(tab1[ii,1], regexec(pattern, tab1[ii,1]))
    vec1 = c(vec1, result[[1]][2])
    
    res <- str_match(tab1[ii,1], "tr\\|\\s*(.*?)\\s*\\|")
    vec2 = c(vec2, res[,2])

    setTxtProgressBar(pb, ii)
}

In [77]:
# create new dataframe
tab2 = cbind(vec1, vec2, tab1[,2:1025])
colnames(tab2) = c('Gene', 'UniProtID', paste0('D', 1:1024))
dim(tab2)
tab2[1:3,]

# another df with just gene names and embeddings
tab3 = tab2[,-2]
tab3 <- tab3[tab3$Gene!='' & !is.na(tab3$Gene),]
dim(tab3)

[1] 21164  1026

Gene   UniProtID  D1         D2          D3            D4         
1 LYPD6B A0A8C3IPM8 0.04380944 0.046668537  0.0196705540 0.010638186
2 VAMP2  A0A8C3HU26 0.04984607 0.108225300  0.1338589800 0.009055086
3 CIRBP  A0A8C3IEI6 0.05070832 0.008752312 -0.0005698819 0.055834074
  D5          D6         D7          D8          ⋯ D1015       D1016      
1 -0.01983896 0.02670864 -0.04212752 -0.09735513 ⋯ -0.01836805 -0.00636565
2 -0.04259114 0.08893719  0.02212998 -0.10179134 ⋯  0.03350077 -0.07541211
3  0.05687802 0.01499634 -0.03940918 -0.06279862 ⋯ -0.05099079 -0.03186566
  D1017        D1018        D1019       D1020       D1021       D1022       
1  0.006043086 -0.082583470  0.04174648  0.04077775 -0.01465437  0.002306046
2 -0.065250990 -0.057196867 -0.02992775 -0.01860927 -0.01088253  0.024169970
3 -0.050541412  0.009177394  0.01107539 -0.01030342  0.02962806 -0.014151822
  D1023         D1024     
1  1.563247e-03 0.02171617
2 -7.653655e-05 0.03049799
3  1.815285e-02 0.01191045

[1] 14486  1025

In [78]:
# save
write.table(tab3, file = 'turtle_embeddings.csv', sep = ',', row.names = F,
           col.names = T, quote = F)

write.table(tab2, file = 'turtle_embeddings_with_Uniprot.csv', sep = ',', 
            row.names = F, col.names = T, quote = F)

In [ ]:
# ..... for lizard ..... #

In [2]:
# load gtf
gtf = read.delim('~/cellranger_10x/AnoSag2.1_withMT.gtf', sep = '\t', comment.char = '#', header = F)
gtf[1:2,]
dim(gtf)

V1             V2     V3         V4     V5     V6 V7 V8
1 NW_026844366.1 Gnomon gene       790335 804913 .  -  . 
2 NW_026844366.1 Gnomon transcript 790335 804913 .  -  . 
  V9                                                                                                                                                                                                                                              
1 gene_id LOC132761864; transcript_id ; db_xref GeneID:132761864; description cytochrome P450 2C44-like; gbkey Gene; gene LOC132761864; gene_biotype protein_coding;                                                                              
2 gene_id LOC132761864; transcript_id XM_060754917.1; db_xref GeneID:132761864; gbkey mRNA; gene LOC132761864; model_evidence Supporting evidence includes similarity to: 2 Proteins; product cytochrome P450 2C44-like; transcript_biotype mRNA;

[1] 1073869       9

In [14]:
# add gene ids to gtf
gtf$gene = NA
pb = txtProgressBar(min = 0, max = dim(gtf)[1], initial = 0)

for(ii in 1:dim(gtf)[1]){
    pattern <- "gene \\s*(.*?)\\s*;"
    result <- regmatches(gtf[ii,9], regexec(pattern, gtf[ii,9]))
    gtf$gene[ii] = result[[1]][2]

    setTxtProgressBar(pb, ii)
}

In [31]:
# add gene ids to gtf
gtf$protein = NA
pb = txtProgressBar(min = 0, max = dim(gtf)[1], initial = 0)

for(ii in 1:dim(gtf)[1]){
    pattern <- "protein_id \\s*(.*?)\\s*;"
    result <- regmatches(gtf[ii,9], regexec(pattern, gtf[ii,9]))
    gtf$protein[ii] = result[[1]][2]

    setTxtProgressBar(pb, ii)
}

In [41]:
# save gtf file with gene name
write.table(gtf, file = '~/cellranger_10x/AnoSag2.1_gtf_gene.txt', sep = '\t',
           row.names = F, col.names = T, quote = F)

In [42]:
# load gtf
gtf = read.delim('~/cellranger_10x/AnoSag2.1_gtf_gene.txt', sep = '\t')
gtf[1,]

V1             V2     V3   V4     V5     V6 V7 V8
1 NW_026844366.1 Gnomon gene 790335 804913 .  -  . 
  V9                                                                                                                                                                 
1 gene_id LOC132761864; transcript_id ; db_xref GeneID:132761864; description cytochrome P450 2C44-like; gbkey Gene; gene LOC132761864; gene_biotype protein_coding; 
  gene         protein
1 LOC132761864 NA

In [20]:
tab1 = fread(paste0(path0, 'Anolis Sagrei.GCF_025583915.1_AnoSag2.1_protein.faa.ProtT5.embeddings.csv.gz'))
tab1 <- tab1[-1,]
dim(tab1)

tab1$transcript = sub('\\ .*', '', unlist(tab1[,1]))
tab1[1:3,]

V1                                                                             
1 XP_060628611.1 polymeric immunoglobulin receptor-like [Anolis sagrei ordinatus]
2 XP_060630910.1 partitioning defective 6 homolog gamma [Anolis sagrei ordinatus]
3 XP_060631285.1 kappa-type opioid receptor [Anolis sagrei ordinatus]            
  V2           V3           V4         V5           V6          V7        
1 -0.002807721  0.030977504 0.06113799  0.004617391 -0.03467397 0.04913078
2 -0.001295051 -0.001717766 0.02265036 -0.007022513  0.01203018 0.03811935
3  0.036000263  0.122104764 0.05079413  0.026990210 -0.00413893 0.01938031
  V8          V9          V10          ⋯ V1017        V1018        V1019       
1 -0.04042948 -0.13137065  0.032248410 ⋯  0.007108381  0.004988837 -0.071039820
2 -0.03509234 -0.06014255 -0.004132324 ⋯  0.009106064 -0.086794650  0.003202471
3 -0.02276496 -0.04582505  0.011989381 ⋯ -0.011796548 -0.001863219 -0.003736525
  V1020       V1021       V1022       V1023       V1024        V1025     
1 -0.03201043  0.00168761 0.040699184  0.03793790  0.094349050 0.05291024
2  0.05110768  0.02963551 0.017490150  0.01466285  0.003511432 0.01413679
3  0.06735080 -0.02616484 0.001190309 -0.01015938 -0.027167782 0.01783289
  transcript    
1 XP_060628611.1
2 XP_060630910.1
3 XP_060631285.1

In [43]:
# add gene ids to gtf
tab1$gene = gtf$gene[match(tab1$transcript, gtf$protein)]
tab1[1:3,]

V1                                                                             
1 XP_060628611.1 polymeric immunoglobulin receptor-like [Anolis sagrei ordinatus]
2 XP_060630910.1 partitioning defective 6 homolog gamma [Anolis sagrei ordinatus]
3 XP_060631285.1 kappa-type opioid receptor [Anolis sagrei ordinatus]            
  V2           V3           V4         V5           V6          V7        
1 -0.002807721  0.030977504 0.06113799  0.004617391 -0.03467397 0.04913078
2 -0.001295051 -0.001717766 0.02265036 -0.007022513  0.01203018 0.03811935
3  0.036000263  0.122104764 0.05079413  0.026990210 -0.00413893 0.01938031
  V8          V9          V10          ⋯ V1018        V1019        V1020      
1 -0.04042948 -0.13137065  0.032248410 ⋯  0.004988837 -0.071039820 -0.03201043
2 -0.03509234 -0.06014255 -0.004132324 ⋯ -0.086794650  0.003202471  0.05110768
3 -0.02276496 -0.04582505  0.011989381 ⋯ -0.001863219 -0.003736525  0.06735080
  V1021       V1022       V1023       V1024        V1025      transcript    
1  0.00168761 0.040699184  0.03793790  0.094349050 0.05291024 XP_060628611.1
2  0.02963551 0.017490150  0.01466285  0.003511432 0.01413679 XP_060630910.1
3 -0.02616484 0.001190309 -0.01015938 -0.027167782 0.01783289 XP_060631285.1
  gene        
1 LOC132773378
2 PARD6G      
3 OPRK1

In [44]:
# create new dataframe
tab3 = cbind(tab1$gene, tab1[,2:1025])
colnames(tab3) = c('Gene', paste0('D', 1:1024))
tab3 <- tab3[tab3$Gene!='' & !is.na(tab3$Gene),]

dim(tab3)
tab3[1:3,]

[1] 35821  1025

Gene         D1           D2           D3         D4           D5         
1 LOC132773378 -0.002807721  0.030977504 0.06113799  0.004617391 -0.03467397
2 PARD6G       -0.001295051 -0.001717766 0.02265036 -0.007022513  0.01203018
3 OPRK1         0.036000263  0.122104764 0.05079413  0.026990210 -0.00413893
  D6         D7          D8          D9           ⋯ D1015        D1016       
1 0.04913078 -0.04042948 -0.13137065  0.032248410 ⋯ -0.021292383  0.007108381
2 0.03811935 -0.03509234 -0.06014255 -0.004132324 ⋯ -0.014923408  0.009106064
3 0.01938031 -0.02276496 -0.04582505  0.011989381 ⋯ -0.001111696 -0.011796548
  D1017        D1018        D1019       D1020       D1021       D1022      
1  0.004988837 -0.071039820 -0.03201043  0.00168761 0.040699184  0.03793790
2 -0.086794650  0.003202471  0.05110768  0.02963551 0.017490150  0.01466285
3 -0.001863219 -0.003736525  0.06735080 -0.02616484 0.001190309 -0.01015938
  D1023        D1024     
1  0.094349050 0.05291024
2  0.003511432 0.01413679
3 -0.027167782 0.01783289

In [45]:
# save
write.table(tab3, file = 'lizard_embeddings.csv', sep = ',', row.names = F,
           col.names = T, quote = F)